In [1]:
%pylab inline
%load_ext autoreload
%autoreload 2

Populating the interactive namespace from numpy and matplotlib


In [2]:
import os, re, sys, io, json, logging, itertools, operator, collections, functools

from glob import glob

import pandas as pd
import numpy as np
# import seaborn as sb
import matplotlib.pyplot as plt
from gensim.models import LdaModel
from elasticsearch import Elasticsearch
from elasticsearch.client.indices import IndicesClient
from elasticsearch import helpers

import pyLDAvis.gensim

/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/funcy/decorators.py:56: DeprecationWarning: inspect.getargspec() is deprecated, use inspect.signature() instead
  spec = inspect.getargspec(func)
/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/funcy/decorators.py:56: DeprecationWarning: inspect.getargspec() is deprecated, use inspect.signature() instead
  spec = inspect.getargspec(func)
/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/funcy/decorators.py:56: DeprecationWarning: inspect.getargspec() is deprecated, use inspect.signature() instead
  spec = inspect.getargspec(func)
/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/funcy/decorators.py:56: DeprecationWarning: inspect.getargspec() is deprecated, use inspect.signature() instead
  spec = inspect.getargspec(func)
/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/funcy/decorators.py:56: DeprecationWarning: inspect.getargspec() is deprecated, use in

In [3]:
sys.path.append('../python/lib/')
sys.path.append('../scripts/')

In [4]:
from build_model import WikiIterator

Requires NRK recomendation Elasticsearch index.

In [5]:
model_fn = '../lda-100-subtitles'
es_hosts = ['localhost:9200']
index = 'reco'
field = 'subtitles'
analyzer = 'no_analyzer'

In [6]:
m = LdaModel.load(model_fn)

Loads the field from the whole index in memory. This is 15000 documnents in the current index.

In [7]:
es = Elasticsearch(hosts=es_hosts)
ic = IndicesClient(es)

docs = []

q = {'query': {'exists': {'field': field}}}

count = 0

for hit in helpers.scan(es, index=index, query=q, _source=[field]):
    source = hit['_source']
    sub = source[field]

    resp = ic.analyze(index=index, body={'analyzer': analyzer, 'text': sub})

    docs.append([token['token'] for token in resp['tokens']])

    count += 1

logging.info("Collected %d documents" % count)

In [8]:
docs = [m.id2word.doc2bow(d) for d in docs] 

In [9]:
vis =  pyLDAvis.gensim.prepare(m, docs, m.id2word)
pyLDAvis.display(vis)

/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/IPython/core/formatters.py:92: DeprecationWarning: DisplayFormatter._ipython_display_formatter_default is deprecated: use @default decorator instead.
  def _ipython_display_formatter_default(self):
/Users/n632848/anaconda/envs/default3/lib/python3.5/site-packages/IPython/core/formatters.py:669: DeprecationWarning: PlainTextFormatter._singleton_printers_default is deprecated: use @default decorator instead.
  def _singleton_printers_default(self):
